# 0. 라이브러리 호출

### 0-1) 라이브러리 호출

In [2]:
import os
import re
import numpy as np
import pandas as pd
import copy
import json
from konlpy.tag import Okt
from gensim.models import Word2Vec
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity

import warnings
warnings.filterwarnings(action='ignore')

### 0-2) 경로 확인

In [3]:
pwd

'C:\\Users\\NY\\Desktop\\KB\\nayeon\\src'

# 1. 모델링

### 1-1) 토큰화
- konlyp - Okt 사용

In [4]:
os.chdir('../data')
os.listdir()

['terms.json', 'terms_tokens.json', 'terms_vectors.json', 'terms_w2v']

In [5]:
pwd

'C:\\Users\\NY\\Desktop\\KB\\nayeon\\data'

In [11]:
okt = Okt()

with open('terms.json', 'r', encoding='utf-8') as f:
    f = f.read()
    data = json.loads(f)

data
# terms = json.dumps(data, ensure_ascii = False)
# terms

{'『KB 군인연금평생안심통장』특약 ': {'제1조 약관의 적용 ': 'KB군인연금평생안심통장(이하 “이 통장”이라 합니다)거래는 이 특약을 적용하고, 이 특약에서 정하지 않은 사항에 대해서는 입출금이자유로운약관, 예금거래기본약관을 순서대로 적용합니다.  ',
  '제2조 예금과목 ': '이 통장의 예금과목은 저축예금으로 합니다. ',
  '제3조 가입대상 ': '이 통장의 가입대상은 실명의 개인으로서 군인연금을 수령하는 고객으로 합니다. ',
  '제4조 입금제한 ': '①  이 통장은 국군재정관리단에서 입금하는 군인연금 급여로 입금자원이 제한되며, 군인연금 급여 이외의 자금은 입금 할 수 없습니다. ② 이 통장으로의 입금은 군인연금법 제 7조, 민사집행법 제 195조, 동법 시행령 제 2조 (이하 “관련 법”이라 합니다)에서 정하는 군인연금 급여 압류금지 대상금액 이하로 입금 건당 금액을 제한합니다.   단, 통장의 잔액은 금액에 제한 없이 유지가 가능하며 입금 제한에 영향을 미치지 않습니다. ③  이 통장으로 매월 수령하는 군인연금 급여액이 관련 법에서 정하는 압류금지 대상금액을 초과하는 경우 압류금지 대상금액까지만 이 통장으로 입금되므로 압류금지 대상금액을 초과한 금액은 입금이 제한되지 않는 별도의 통장으로 수령해야 합니다. ',
  '제5조 거래제한 ': '① 이 통장은 관련 법에 따라 입금된 예금과 이에 관한 채권을 압류할 수 없고, 압류에 의한 지급제한이 되지  않습니다. ② 이 통장은 은행이 상계할 수 없습니다 ③ 이 통장은 양도 및 담보제공 할 수 없습니다 ④ 이 통장은 통장자동대출계좌로 사용할 수 없습니다. ⑤ 이 통장을 신용카드 결제계좌나 공과금 등 대금납부 목적의 계좌로 지정한 경우에 결제ㆍ납부 금액이  부족하거나 결제ㆍ납부 취소 등이 발생한 때에는 제4조에 따라 고객이 영업점 창구에서 결제ㆍ납부금액을  직접 납부하거나 별도 지정계좌로 입금 또는 직접 수령하는 방법으로 처리하여야 합니다. ⑥ 인터넷뱅킹을 통한 예·부적금 신규시 모계좌로 출

In [12]:
keys = list(data.keys())
keys

['『KB 군인연금평생안심통장』특약 ',
 '「KB 굿플랜적금」특약 ',
 '「KB 나라사랑우대통장」 특약 ',
 '「KB나라사랑적금(직업군인용)」특약 ',
 '「KB나라사랑적금(직업군인용)」특약',
 '「KB내맘대로적금」특약 ',
 '「KB내맘대로프리랜서통장」특약 ',
 '플러스사랑단체보험 보통약관 ',
 '「KB 더블모아 예금」 특약 ',
 '「KB 두근두근여행적금」 특약 ',
 'KB두레통장  특약 ',
 '「KB드림톡적금」특약 ',
 '~ 「KB리브와 함께 매일매일적금」특약 ',
 '「KB마음편한통장」특약   ',
 '「KB마이핏통장」 특약 ',
 '「KB 맑은바다적금」 특약 ',
 '「KB 맑은하늘적금」 특약 ',
 '「KB 매직카적금」특약 ',
 '「KB미소드림적금」특약  ',
 '「KB반려행복적금」 특약 ',
 '『KB 뱅크월렛통장』특약 ',
 '「KB보육&복지시설우대통장」특약 ',
 '「KB보증서 담보대출 입금전용통장」 특약 ',
 '『KB부가세납부전용통장』특약 ',
 'KB사랑나눔통장특약 ',
 '「KB사랑나눔적금」특약 ',
 '『KB 사학연금평생안심통장』특약 ',
 '「KB 상호부금」  특약 ',
 '「KB 선생님든든적금」 특약 ',
 '「KB아내사랑적금」특약 ',
 '「KB아시아나ONE통장」특약 ',
 '『KB 압류방지전용통장』 특약 ',
 '「KB어린이집&유치원통장」특약 ',
 '「KB연금우대적금」특약 ',
 '「KB연구비통장」 특약 ',
 '「KB온라인우대통장」특약 ',
 'KB우대기업통장특약 ',
 'KB우대저축통장특약 ',
 '「KB이지바로 연구비통장」특약 ',
 '「KB장병내일준비적금」 특약 ',
 'KB종합통장특약 ',
 '「KB 주거행복 월세통장」 특약 ',
 '「KB주니어Star적금」특약 ',
 '「KB주니어Star통장」특약 ',
 '「KB주니어라이프적금」특약 ',
 '「KB주니어라이프증여예금」특약 ',
 '「KB 주니어라이프통장」 특약 ',
 '『KB 주택연금지킴이통장』특약 ',
 '「KB 증권 공모주 1.5 배 정기예금」 

In [257]:
data2 = copy.deepcopy(data)

In [258]:
%time

words = []

for i in range(len(keys)):
    for key, value in data2[keys[i]].items():
        tokens = okt.nouns(value)
        temp = []
        for token in tokens:
            if len(token) < 2:
                continue
            else:
                temp.append(token)
        data2[keys[i]][key] = temp
    words.append(temp)

data2

CPU times: total: 0 ns
Wall time: 998 µs


{'『KB 군인연금평생안심통장』특약 ': {'제1조 약관의 적용 ': ['군인',
   '연금',
   '평생',
   '안심',
   '통장',
   '이하',
   '통장',
   '거래',
   '특약',
   '적용',
   '특약',
   '사항',
   '대해',
   '입출금',
   '약관',
   '예금',
   '거래',
   '약관',
   '순서대로',
   '적용'],
  '제2조 예금과목 ': ['통장', '예금', '과목', '저축예금'],
  '제3조 가입대상 ': ['통장', '가입', '대상', '실명', '개인', '군인', '연금', '수령', '고객'],
  '제4조 입금제한 ': ['통장',
   '국군',
   '재정',
   '관리',
   '입금',
   '군인',
   '연금',
   '급여',
   '입금자',
   '제한',
   '군인',
   '연금',
   '급여',
   '이외',
   '자금',
   '입금',
   '통장',
   '입금',
   '군인',
   '연금',
   '민사집행법',
   '시행',
   '이하',
   '관련',
   '군인',
   '연금',
   '급여',
   '압류',
   '금지',
   '대상',
   '금액',
   '이하',
   '입금',
   '금액',
   '제한',
   '통장',
   '잔액',
   '금액',
   '제한',
   '유지',
   '입금',
   '제한',
   '영향',
   '통장',
   '매월',
   '수령',
   '군인',
   '연금',
   '급여',
   '관련',
   '압류',
   '금지',
   '대상',
   '금액',
   '초과',
   '경우',
   '압류',
   '금지',
   '대상',
   '금액',
   '통장',
   '입금',
   '압류',
   '금지',
   '대상',
   '금액',
   '초과',
   '금액',
   '입금',
   '제한',
   '별도',
   '통장',


In [ ]:
with open('terms_tokens.json', 'w', encoding='utf-8') as f:
    json.dump(data2, f)

# with open('data_tokens.json', 'r', encoding='utf-8') as f:
#   f = f.read()
#   data = json.loads(f)

# json.dumps(data, ensure_ascii = False)

### 1-2) 벡터화
- gensim - Word2Vec 사용

In [20]:
model = Word2Vec(words, min_count=1, window=3, workers=3, seed=1) 
model.save('terms_w2v')

In [259]:
model = Word2Vec.load('terms_w2v')

word_dict = {}
for vocab in model.wv.index_to_key:
    word_dict[vocab] = model.wv[vocab]

word_dict

{'예금': array([-0.7840744 ,  0.9417485 ,  0.24292298,  0.1525625 , -0.15808246,
        -0.86258537,  0.3122231 ,  0.65171087, -0.19468473, -0.44576955,
        -0.22760901, -0.9759974 ,  0.45671585, -0.03873695,  0.18593162,
        -0.65208614, -0.08228103, -0.62640584,  0.2230946 , -0.7064098 ,
         0.19162017,  0.7217043 ,  0.12682809, -0.32523993, -0.06067123,
         0.04101607, -0.12470974, -0.15913364, -0.6582352 , -0.73003113,
         0.14836304,  0.03905761,  0.4371993 ,  0.20737135, -0.6512803 ,
         0.70688534,  0.20452988, -0.37534106, -0.26763952, -0.8896159 ,
         0.42848665, -0.23717628, -0.72496706, -0.46155515,  0.44978547,
        -0.05084841, -0.12419987, -0.5189899 ,  0.10068885, -0.17205562,
         0.00338524, -0.46824756,  0.16691175, -0.14054613,  0.12767155,
         0.0623537 ,  0.6430186 , -0.22188225, -0.47287807, -0.05787888,
         0.39464468,  0.09946648,  0.5938471 , -0.30450347, -0.2628582 ,
         0.5820349 , -0.25293502,  0.7182678 

In [16]:
data3 = copy.deepcopy(data2)

In [17]:
%time

for i in range(len(keys)):
    for key, value in data3[keys[i]].items():
        vector_list = []
        for word in value:
            if word in word_dict.keys():
                vector_list.append(word_dict[word])
        data3[keys[i]][key] = np.sum(vector_list, axis=0).tolist()      

data3

CPU times: total: 0 ns
Wall time: 0 ns


{'『KB 군인연금평생안심통장』특약 ': {'제1조 약관의 적용 ': [-10.248276710510254,
   15.597399711608887,
   4.569143295288086,
   0.7270921468734741,
   -1.1712603569030762,
   -14.856080055236816,
   4.926259517669678,
   10.577014923095703,
   -3.6777617931365967,
   -6.382809162139893,
   -3.7915725708007812,
   -15.333837509155273,
   7.025262832641602,
   0.10918808728456497,
   4.055466175079346,
   -10.533982276916504,
   -1.6699191331863403,
   -9.92856502532959,
   5.017956256866455,
   -12.558915138244629,
   2.9600541591644287,
   9.977884292602539,
   1.764474868774414,
   -5.2303080558776855,
   -3.375869035720825,
   0.9942861795425415,
   -1.2239267826080322,
   -1.9709672927856445,
   -10.236098289489746,
   -9.763236045837402,
   4.762924671173096,
   0.5843322277069092,
   6.2149763107299805,
   3.524090051651001,
   -8.027713775634766,
   11.87381362915039,
   3.5127933025360107,
   -5.160458087921143,
   -4.583578586578369,
   -14.781481742858887,
   5.932644367218018,
   -4.35539722442

In [104]:
with open('terms_vectors.json', 'w', encoding='utf-8') as f:
    json.dump(data3, f)

# with open('data_vectors.json', 'r', encoding='utf-8') as f:
#   f = f.read()
#   data = json.loads(f)

# json.dumps(data, ensure_ascii = False)

### 1-3) 문서 검색
- TF-IDF 사용

In [86]:
title = list(data.keys())
title = [' '.join(okt.nouns(t)) for t in title]
title

['군인 연금 평생 안심 통장 특약',
 '굿 플랜 적금 특약',
 '나라 사랑 우대 통장 특약',
 '나라 사랑 적금 직업 인용 특약',
 '나라 사랑 적금 직업 인용 특약',
 '맘 적금 특약',
 '맘 프리랜서 통장 특약',
 '플러스 사랑 단체 보험 보통 약관',
 '더블 예금 특약',
 '여행 적금 특약',
 '두레 통장 특약',
 '드림 톡 적금 특약',
 '리브 매일 적금 특약',
 '마음 통장 특약',
 '마이 핏 통장 특약',
 '맑은 바다 적금 특약',
 '맑은 하늘 적금 특약',
 '매직 카 적금 특약',
 '미소 드림 적금 특약',
 '반려 행복 적금 특약',
 '뱅크 월렛 통장 특약',
 '보육 복지 시설 우대 통장 특약',
 '보증 담보 대출 입금 전용 통장 특약',
 '부가세 납부 전용 통장 특약',
 '사랑 나눔 통장 특약',
 '사랑 나눔 적금 특약',
 '사학 연금 평생 안심 통장 특약',
 '상호 부금 특약',
 '선생님 적금 특약',
 '아내 사랑 적금 특약',
 '아시아나 통장 특약',
 '압류 방지 전용 통장 특약',
 '어린이집 유치원 통장 특약',
 '연금 우대 적금 특약',
 '비통 특약',
 '온라인 우대 통장 특약',
 '우대 기업 통장 특약',
 '우대 저축 통장 특약',
 '지바 비통 특약',
 '장병 준비 적금 특약',
 '종합 통장 특약',
 '주거 행복 월세 통장 특약',
 '주니어 적금 특약',
 '주니어 통장 특약',
 '주니어 라이프 적금 특약',
 '주니어 라이프 증여 예금 특약',
 '주니어 라이프 통장 특약',
 '주택연금 지킴 통장 특약',
 '증권 모주 배 정기예금 특약',
 '증권 통장 특약',
 '직장인 우대 적금 특약',
 '짝꿍 통장 특약',
 '창조 금융 예금 특약',
 '청년 희망 적금 특약',
 '쿠폰 북 적금 특약',
 '통일기 적금 특약',
 '퇴직 연금 정기예금 특약',
 '티몬 적금 특약',
 '트리플 빙상 여제 정기예금 특약',
 '펀드 예금 특약',
 '펫코 노미 적

In [87]:
tfidf = TfidfVectorizer()
tfidfv = tfidf.fit_transform(title)

In [275]:
user_input = input('검색어를 입력하세요: ')

tokenized_input = okt.nouns(user_input)
input_tokens = ' '.join(tokenized_input)

검색어를 입력하세요: 주니어통장 가입대상


In [276]:
similarity = {}
for i in range(len(title)):
    sim = cosine_similarity(tfidf.transform([input_tokens]).toarray(), 
                                 [i.toarray() for i in tfidfv][i])
    similarity[keys[i]] = float(sim)

# similarity

In [277]:
similarity = {key: value for key, value in sorted(similarity.items(), key=lambda item: item[1], reverse=True)}
rating = [str(key) for key, value in sorted(similarity.items(), key=lambda item: item[1], reverse=True)]
top = rating[:3]

top

['「KB주니어Star통장」특약 ', '「KB주니어Star적금」특약 ', '「KB 주니어라이프통장」 특약 ']

In [278]:
result = {}
for i in top:
    result[i] =  str(abs(round(similarity[i]*100, 2))) + '%'

result

{'「KB주니어Star통장」특약 ': '97.3%',
 '「KB주니어Star적금」특약 ': '77.92%',
 '「KB 주니어라이프통장」 특약 ': '75.38%'}

### 1-4) 조문 검색
- Word2Vec 사용 
- (코드 수정 필요)

In [279]:
title_top = top[0]
title_top

'「KB주니어Star통장」특약 '

In [281]:
tokenized_input = okt.nouns(user_input)

input_vector = []

for token in tokenized_input:
    if token in word_dict.keys():
        input_vector.append(word_dict[token])

if len(input_vector) != 0:
    user_vector = (np.sum(input_vector, axis=0) / len(input_vector)).tolist()
else:
    user_vector = 0

# user_vector

In [282]:
detail_similarity = {}

if user_vector == 0:
    result = 0
else:
    for key, value in data3[title_top].items():
        try:
            detail_sim = cosine_similarity(np.array(user_vector).reshape(1, -1), 
                                           np.array([float(i) if i != '.' else float('0.0') for i in str(value)[1:-1].split(',')]).reshape(1, -1))
        except:
            detail_sim = 0
        detail_similarity[key] = float(detail_sim)

In [283]:
detail_similarity = {key: value for key, value in sorted(detail_similarity.items(), key=lambda item: item[1], reverse=True)}
detail_rating = [str(key) for key, value in sorted(detail_similarity.items(), key=lambda item: item[1], reverse=True)]
detail_top = detail_rating[:3]

detail_top

['제2조 가입대상 ', '제4조 자동전환 ', '제9조 스윙서비스 (Swing Service) ']

In [284]:
result = {}
for i in detail_top:
    result[f'{title_top}-{i}'] = str(abs(round(detail_similarity[i]*100, 2))) + '%'

result

{'「KB주니어Star통장」특약 -제2조 가입대상 ': '99.8%',
 '「KB주니어Star통장」특약 -제4조 자동전환 ': '94.57%',
 '「KB주니어Star통장」특약 -제9조 스윙서비스 (Swing Service) ': '92.7%'}

In [291]:
print(title_top, '\n')

for i in detail_top:
    print(f'{i}: {data[title_top][i]}\n')

「KB주니어Star통장」특약  

제2조 가입대상 : 이 통장의 가입대상은 만 18세 미만인 실명의 개인으로 1인1통장에 한합니다. 

제4조 자동전환 :   ①  이  통장은  가입자의  연령이  만  20세에  도달하는  해의  첫  영업일에  「KB  Star*t  통장」으로 자동전환됩니다.   ② 제1항에 의한 자동전환시에「KB Star*t 통장」을 이미 보유한 경우에는 「KB종합 통장」 으로 전환됩니다. 

제9조 스윙서비스 (Swing Service) : ①  이  통장  가입자가「스윙서비스」를  신청하는  경우,  가입자가  지정한  일자의  영업  종료  후  이 통장의  잔여금액  중  3만원  이상  1천원  단위로  최대  1백만원까지  자동  출금하여  이  통장과 연결된 「KB주니어Star적금」으로 매월 이체합니다.  ② 지정일이 영업일이 아닌 때는 그 다음 영업일에 제1항의 이체거래를 합니다. ③  이  통장에  압류,  사고신고  등  예금의  지급불능  사유가  발생할  경우  스윙서비스는  제공되지 않습니다. ④ 이 통장 가입자가 스윙서비스 신청내용을 변경 또는 해지하고자 할 때는 이체지정일 전영업일까지 은행에 신고해야 합니다. 

